<a href="https://colab.research.google.com/github/frohsch/MathSolverAI/blob/main/Idefics2_SFT.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

##Team2
MathVerse 데이터셋 다운로드 (주요 항목: vision dominant)

학습/평가셋 구분 (구분: 평가셋 instance 100~n00개 정도로 구성)

idefics2로 베이스라인 평가

각 문항 별 자동 생성 결과 수집 (-> finetune)


# Drive mount

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# install

In [ ]:
!pip install datasets
!pip install transformers
!pip install torch torchvision
!pip install peft
!pip install trl accelerate
!pip install bitsandbytes

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.3/527.3 kB 28.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 57.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 17.5 MB/s eta 0:00:00
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 14.0.2
    Uninstalling pyarrow-14.0.2:
      Successfully uninstalled pyarrow-14.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24.4.1 requires pyarrow<15.0.0a0,>=14.0.1, but you have pyarrow 17.0.0 which is incompatible.
ibis-framework 8.0.0 requires pyarrow<16,>=2, but you have pyarrow 17.0.0 which is incompatible.
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manyli

# import

In [ ]:
import torch
from sklearn.model_selection import train_test_split
from datasets import load_dataset, DatasetDict
from torch.utils.data import DataLoader, Dataset
from transformers import AutoTokenizer, AutoModelForVision2Seq, AutoProcessor
from torchvision import transforms  #tensor변환
from PIL import Image
import json
import requests
import gc
from peft import LoraConfig, get_peft_model
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score
from trl import SFTConfig, SFTTrainer
import numpy as np
from copy import deepcopy

# dataset load

In [ ]:
#데이터셋 로드
dataset = load_dataset("AI4Math/MathVerse", "testmini")

#split
dataset = dataset['testmini']
train_dataset, eval_dataset = train_test_split(dataset, test_size=0.1, shuffle=True, random_state=42)

KeyboardInterrupt: 

In [ ]:
# 데이터셋 로드
dataset = load_dataset("AI4Math/MathVerse", "testmini")

# 데이터셋을 train과 eval로 분할
split_dataset = dataset["testmini"].train_test_split(test_size=0.1, shuffle=True, seed=42)

# 분할된 데이터셋 확인
train_dataset = split_dataset['train']
eval_dataset = split_dataset['test']


In [ ]:
print(train_dataset)

{'sample_index': ['2330', '747', '310', '267', '1445', '2563', '3164', '64', '3745', '1259', '3504', '3708', '145', '3407', '2357', '2601', '3724', '2949', '2058', '439', '3637', '3397', '3159', '3730', '3140', '252', '3564', '818', '433', '2179', '2878', '2047', '3084', '280', '2471', '3048', '3050', '359', '2785', '300', '3425', '977', '1968', '2511', '3028', '2937', '1238', '416', '2426', '3700', '569', '2112', '3779', '1150', '309', '1488', '2749', '1616', '2731', '1042', '3832', '2969', '721', '3751', '3062', '965', '786', '1887', '1937', '59', '77', '2196', '369', '2619', '3785', '1645', '1748', '3531', '2677', '3368', '803', '2284', '2269', '3506', '3721', '3752', '1860', '2358', '1106', '125', '315', '2755', '306', '2908', '1177', '3045', '2222', '3077', '430', '2000', '1092', '1447', '45', '730', '1565', '3802', '2004', '2119', '3294', '1193', '1784', '3889', '1179', '388', '31', '3890', '3306', '204', '3190', '3800', '2150', '2212', '2141', '3285', '479', '3520', '1012', '444

In [ ]:
print(type(train_dataset))
print(type(eval_dataset))

<class 'datasets.arrow_dataset.Dataset'>
<class 'datasets.arrow_dataset.Dataset'>


# model, processor load

In [ ]:
#32비트 모델 로드
#model = AutoModelForVision2Seq.from_pretrained("HuggingFaceM4/idefics2-8b")
#processor = AutoProcessor.from_pretrained("HuggingFaceM4/idefics2-8b")

#8비트 모델 로드
#model = AutoModelForVision2Seq.from_pretrained("HuggingFaceM4/idefics2-8b", load_in_8bit=True, device_map = 'auto')
#processor = AutoProcessor.from_pretrained("HuggingFaceM4/idefics2-8b", load_in_8bit=True)

#16비트 모델 로드
model = AutoModelForVision2Seq.from_pretrained("HuggingFaceM4/idefics2-8b", torch_dtype=torch.float16, device_map = 'auto')
processor = AutoProcessor.from_pretrained("HuggingFaceM4/idefics2-8b", torch_dtype=torch.float16)

# LoRA 설정 추가
lora_config = LoraConfig(
    r=8,  # 랭크 크기
    lora_alpha=16,  # 스케일링 파라미터
    target_modules=["q_proj", "k_proj", "v_proj", "o_proj"],  # LoRA 적용 대상 모듈
    lora_dropout=0.1,  # 드롭아웃 확률
    task_type="CAUSAL_LM",
    bias="none"  # 바이어스 처리 방식
)
model = get_peft_model(model, lora_config)

for name, param in model.named_parameters():
    if "lora" in name:
        param.requires_grad = True
    else:
        param.requires_grad = False

model = model.to("cuda")
device = 'cuda'

config.json:   0%|          | 0.00/684 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/74.4k [00:00<?, ?B/s]

model-00001-of-00007.safetensors:   0%|          | 0.00/4.64G [00:00<?, ?B/s]

model-00002-of-00007.safetensors:   0%|          | 0.00/4.99G [00:00<?, ?B/s]

model-00003-of-00007.safetensors:   0%|          | 0.00/4.90G [00:00<?, ?B/s]

...

tokenizer.model:   0%|          | 0.00/493k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.80M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/92.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/1.04k [00:00<?, ?B/s]

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


[https://huggingface.co/docs/transformers/main/ko/perf_infer_gpu_one]

In [ ]:
demo_prompt_extract = """
I am providing you a response from a model to a math problem, termed 'Model Response'. You should extract the answer from the response as 'Extracted Answer'. Directly output the extracted answer with no explanation.

1.
Model response: 'Rounded to two decimal places, the perimeter of the sector is approximately:\n\n(-2, 1)'
Extracted Answer: (-2, 1)

2.
Model response: 'at those points.\n\nTherefore, the correct option that represents the meaning of the intersection points of the graphs is:\n\nD. They give the solutions to the equation $f(t)=g(t)$.",'
Extracted Answer: D

3.
Model response: ' at 1 (there's a closed circle at y = 1), the range in interval notation is \\((-4, 1]\\).\n\nFinal values:\nDomain: \\((-3, 3]\\)\nRange: \\((-4, 1]\\)'
Extracted Answer: Domain: \\((-3, 3]\\)\nRange: \\((-4, 1]\\)

4.
Model response: 'As it stands, I cannot provide the correct option letter because there isn't enough information to solve for 'y'.'
Extracted Answer: null

5.
Model response: 'Given that AB = 17.6 meters, we can now substitute into the equation:\n\nd = 17.6 / cos(38\u00b0)\n\nTherefore, to one decimal place, the distance d between Ned and Bart is approximately 22.3 meters.'
Extracted answer: 22.3

6.
Model response:  have all the coefficients for the quadratic function:\n\\( f(x) = ax^2 + bx + c \\)\n\\( f(x) = -1x^2 - 2x + 1 \\)\n\nTherefore, the equation for the graphed function \\( f \\) is:\n\\( f(x) = -x^2 - 2x + 1 \\)"'
Extracted answer: f(x) = -x^2 - 2x + 1

7.
"""



demo_prompt_score = """
Below are two answers to a math question. Question is [Question], [Standard Answer] is the standard answer to the question, and [Model_answer] is the answer extracted from a model's output to this question.  Determine whether these two answers are consistent.
Please note that only when the [Model_answer] completely matches the [Standard Answer] means they are consistent. For non-multiple-choice questions, if the meaning is expressed in the same way, it is also considered consistent, for example, 0.5m and 50cm.
If they are consistent, Judement is 1; if they are different, Judement is 0.

[Question]: Write the set of numbers represented on the number line in interval notation.
[Standard Answer]: (-2,1]
[Model_answer] : Extracted Answer: \\((-2, 1)\\)
Judgement: 0

[Question]: As shown in the figure, circle O has a radius 1.0, if angle BAC = 60.0, then the length of BC is ()\nChoices:\nA:2\nB:2\u221a{{3}}\nC:\u221a{{3}}\nD:2\u221a{{2}}
[Standard Answer]: C
[Model_answer] : B:2\u221a{{3}}
Judgement: 0

[Question]: Find the domain and range of the function f using interval notation.
[Standard Answer]: domain: [-4, 0) and range: (-3, 1]
[Model_answer] : Range: \\((-4, 1]\\)
Judgement: 0

[Question]: As shown in the figure, circle O has a radius 1.0, if angle BAC = 60.0, then the length of BC is ()\nChoices:\nA:2\nB:2\u221a{{3}}\nC:\u221a{{3}}\nD:2\u221a{{2}}
[Standard Answer]: C
[Model_answer] : null
Judgement: 0

[Question]: Given the graph of the ellipse that intersects with x-axis at 9 and -9 and with y-axis at 3 and -3, determine its equation.A. \\frac{{x^2}}{{81}} + \\frac{{y^2}}{{9}} = 1 B. Can not determine.\n
[Standard Answer]: A
[Model_answer] : \\frac{{x^2}}{{81}} + \\frac{{y^2}}{{9}} = 1
Judgement: 1

[Question]: {question}
[Standard Answer]: {gt}
[Model_answer] : {extraction}
Judgement: """

In [ ]:

# 데이터셋 전처리 함수
def preprocess_function(examples):
    questions = examples['query_cot']
    answers = [str(ans) for ans in examples['answer']]
    inputs = [demo_prompt_extract.format(question=q) for q in questions]

        # Prepare the input for the chat template
    prompt = [
        {
            "role": "user",
            "content": [{"type": "image"}, {"type": "text", "text": examples["query_cot"]}],
        },
    ]
    chosen = [
        {
            "role": "assistant",
            "content": [{"type": "text", "text": examples["answer"]}],
        },
    ]
    # rejected = [
    #     {
    #         "role": "assistant",
    #         "content": [{"type": "text", "text": example["rejected"]}],
    #     },
    # ]

    # Apply the chat template
    prompt = processor.apply_chat_template(prompt, tokenize=False)
    chosen = processor.apply_chat_template(chosen, tokenize=False)
    # rejected = processor.apply_chat_template(rejected, tokenize=False)
    # Resize the image to ensure it fits within the maximum allowable
    # size of the processor to prevent OOM errors.
    max_size = processor.image_processor.size["longest_edge"]
    for i in range(len(examples["image"])):
        examples["image"][i].thumbnail((max_size, max_size))
    return {"images": [examples["image"]], "prompt": prompt, "chosen": chosen}


    # print(inputs[0])
    # return

    # Tokenize the prompt text
    model_inputs = tokenizer(inputs, max_length=MAX_LEN, truncation=True, padding='max_length', return_tensors="pt")
    labels = tokenizer(answers, max_length=MAX_LEN, truncation=True, padding='max_length', return_tensors="pt")

    # model_inputs['labels'] = labels['input_ids']
    return {
        'input_ids': model_inputs['input_ids'], \
        'attention_mask': model_inputs['attention_mask'], \
        'labels': labels['input_ids']
    }


# 전처리 적용
tokenized_train_dataset = train_dataset.map(preprocess_function, batched=True, remove_columns=['query_cot', 'answer'])
tokenized_test_dataset = eval_dataset.map(preprocess_function, batched=True, remove_columns=['query_cot', 'answer'])

Map:   0%|          | 0/3546 [00:00<?, ? examples/s]

TypeError: Provided `function` which is applied to all elements of table returns a `dict` of types [<class 'list'>, <class 'str'>, <class 'str'>]. When using `batched=True`, make sure provided `function` returns a `dict` of types like `(<class 'list'>, <class 'numpy.ndarray'>, <class 'pandas.core.series.Series'>, <class 'tensorflow.python.framework.tensor.Tensor'>, <class 'torch.Tensor'>, <class 'jax.Array'>)`.

# Data Collator

In [ ]:
class Idefics2DataCollator:
    def __init__(self, processor):
        self.processor = processor
    def __call__(self, batch):
        texts = []
        images = []
        for example in examples:
            messages = example["messages"]
            text = self.processor.tokenizer.apply_chat_template(
                messages, tokenize=False, add_generation_prompt=False
            )
            texts.append(text)
            images.append(example["images"][0])

        batch = self.processor(texts, images, return_tensors="pt", padding=True)

        labels = batch["input_ids"].clone()
        if self.processor.tokenizer.pad_token_id is not None:
            labels[labels == self.processor.tokenizer.pad_token_id] = -100
        batch["labels"] = labels

        return batch

data_collator = Idefics2DataCollator(processor)

# SFT Settings

In [ ]:
def main():

    global new_train_ds

    def format(example):
        # Prepare the input for the chat template
        prompt = [{"role": "user", "content": [{"type": "image"}, {"type": "text", "text": example["query_cot"]}]}]
        chosen = [{"role": "assistant", "content": [{"type": "text", "text": example["answer"]}]}]
        rejected = [{"role": "assistant", "content": [{"type": "text", "text": example["rejected"]}]}]
        # Apply the chat template
        prompt = processor.apply_chat_template(prompt, tokenize=False)
        chosen = processor.apply_chat_template(chosen, tokenize=False)
        rejected = processor.apply_chat_template(rejected, tokenize=False)
        # Resize the image to ensure it fits within the maximum allowable
        # size of the processor to prevent OOM errors.
        max_size = processor.image_processor.size["longest_edge"] // 2
        example["image"].thumbnail((max_size, max_size))
        return {"images": [example["image"]], "prompt": prompt, "chosen": chosen, "rejected": rejected}

    # Apply the formatting function to the dataset
    new_train_ds = new_train_ds.map(format, remove_columns=new_train_ds.column_names, num_proc=32)


    # Make sure that the images are decoded, it prevents from storing bytes.
    # More info here https://github.com/huggingface/blog/pull/2148#discussion_r1667400478
    f = new_train_ds.features
    f["images"] = features.Sequence(features.Image(decode=True))
    new_train_ds = new_train_ds.cast(f)


    trainer.train()


if __name__ == "__main__":
    main()


In [ ]:
from trl import SFTTrainer
from transformers import TrainingArguments, AutoModelForCausalLM


training_args = TrainingArguments(
    output_dir="./output",
    num_train_epochs=3,
    per_device_train_batch_size=4,
    gradient_accumulation_steps=4,
    optim="paged_adamw_32bit",
    save_steps=700,
    logging_steps=25,
    learning_rate=2e-4,
    fp16=True,
    #max_grad_norm=0.5,
    lr_scheduler_type="cosine",
    warmup_ratio=0.05,
    weight_decay=0.001,
)
print(type(train_dataset))
print(type(eval_dataset))

trainer = SFTTrainer(
    model=model,
    train_dataset=train_dataset,
    eval_dataset=eval_dataset,
    tokenizer=processor.tokenizer,
    args = training_args,
    #data_collator=data_collator,
    dataset_text_field="query_cot"
)

try:
    trainer.train()
except Exception as e:
    print(f"훈련 중 예외 발생: {e}")

#trainer.save_model(training_args.output_dir)

# tokenizer 복사
new_tokenizer = deepcopy(processor)

'''
for key, value in new_tokenizer.init_kwargs.items():
    if isinstance(value, np.dtype):
        new_tokenizer.init_kwargs[key] = value.name
'''
# 복사된 tokenizer 저장
#new_tokenizer.save_pretrained(training_args.output_dir)

<class 'datasets.arrow_dataset.Dataset'>
<class 'datasets.arrow_dataset.Dataset'>


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': dataset_text_field. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:289: UserWarning: You didn't pass a `max_seq_length` argument to the SFTTrainer, this will default to 1024
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:318: UserWarning: You passed a `dataset_text_field` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:408: UserWarning: You passed a tokenizer with `padding_side` not equal to `right` to the SFTTrainer. This might lead to some unexpected behaviour due to overf

훈련 중 예외 발생: Object of type dtype is not JSON serializable


'\nfor key, value in new_tokenizer.init_kwargs.items():\n    if isinstance(value, np.dtype):\n        new_tokenizer.init_kwargs[key] = value.name\n'

In [ ]:
eval_results = trainer.evaluate()
print(f"Perplexity: {torch.exp(torch.tensor(eval_results['eval_loss']))}")
print(f"Evaluation Results: {eval_results}")

Perplexity: 1.330873727798462
Evaluation Results: {'eval_loss': 0.2858356833457947}


## prompt.py

In [ ]:
#수정중
prompt = """
"You are a teacher who explains math problems and provides answers. You must follow the format 'The answer is: [answer]' at the end of your explanation.”

Q: Please first conduct reasoning, and then answer the question and provide the final value, e.g., 1, 2.5, 300, at the end. Write the equation for the piecewise function symmetric to x=3, which goes through (3,0) and (0, 3).
A: To find the equation of the line symmetric to x=3, which goes through (3,0) and (0, 3), we can use the x-coordinate of the points and the midpoint formula. The midpoint of (3,0) and (0,3) is (1.5,1.5). The equation of the line passing through (1.5,1.5) and (0,3) is y - 1.5 = 1.5 - 3 = -1.5. The equation of the line passing through (1.5,1.5) and (3,0) is y - 1.5 = 3 - 1.5 = 1.5. The equation of the line passing through (0,3) and (3,0) is y - 3 = 3 - 0 = 3. Combining these equations, we get the equation of the line symmetric to x=3, which goes through (3,0) and (0, 3):y = 1.5x - 1.5. So, the equation of the line is y = 1.5x - 1.5. The answer is: y=1.5x-1.5

Q: Please first conduct reasoning, and then answer the question and provide the final value, e.g., 1, 2.5, 300, at the end. The graph shows an angle $a$ in standard position with its terminal side intersecting the figure at P. Find the value of $\\cos a$.
A: The $x$-coordinate of P is 21, so we have $\\cos a = \\frac{21}{29}$. The answer is: $\\frac{21}{29}$
f
Q: Please first conduct reasoning, and then answer the question and provide the final value, e.g., 1, 2.5, 300, at the end. Two linear functions are graphed. Consider the graph of $y=4-x$. If the graph is translated 10 units up, what will be the coordinates of the new $y$-intercept? State the coordinates in the form $(a, b)$.
A: To translate the graph 10 units up, we add 10 to the constant term of the equation $y=4-x$.So, the new equation is $y=4-x+10$.Simplifying, we have $y=14-x$.The new $y$-intercept occurs when $x=0$, so the new $y$-intercept is $\\boxed{(0,14)}$.The answer is: (0,14)

Q: Please first conduct reasoning, and then answer the question and provide the final value, e.g., 1, 2.5, 300, at the end. Find the area of the circle shown, correct to one decimal place.
A: The radius of the circle is 6 cm. So, the area of the circle is $3.14 * 6^2 = 3.14 * 36 = 113.04$. The answer is: 113.04."

Q: Please first conduct reasoning, and then answer the question and provide the correct option letter, e.g., A, B, C, D, at the end. As shown in the figure, circle O ia tangent to AB at point C, then S_triangle CDE is (). Choices: A:6√{5}, B:6√{3}, C:6√{2}, D:6
A: Let's think about the multi-choice question. S_triangle CDE = √{3} * 60 = 6√{3}. The answer is: B

Q: Please first conduct reasoning, and then answer the question and provide the correct option letter, e.g., A, B, C, D, at the end. Find x.Choices: A:0.5, B:1, C:1.5, D:2.
A:To solve this problem, use the equation of the line for each of the parallel lines. For the first line, y = 2x + 3. For the second line, y = 3y + 1. For the third line, y = -2x + 2. From the first line, we know that x = 0.5. The answer is: A

Q: {question}
A:
"""

# inference & evaluation (w/o key-value caching)

In [ ]:
import pandas as pd

# 데이터 예시
data = {
    '문제 번호': [1, 2, 3, 4],
    'true_answer': [10, 20, 30, 40],
    'our_answer': [10, 25, 30, 35]
}

# 데이터프레임 생성
df = pd.DataFrame(data)

# true_answer와 our_answer 비교하여 결과 열 추가
df['비교 결과'] = df.apply(lambda row: '같음' if row['true_answer'] == row['our_answer'] else '다름', axis=1)

# 결과 출력
print(df)

In [ ]:
import re
import gc
'''
matches[-1]에서 추출하도록 -> 정상적 작동
([0]에서 하도록 하니 당연히 첫번째 demo prompt에서만 추출했던 것)
'''
def extract_answer(output_text):
    pattern = r"The answer is[:]*\s*([^\n]*)[.]"
    matches = re.findall(pattern, output_text, re.DOTALL)
    return matches[-1].strip() if matches else None

def compare_answers(example):
    example['compare_answer'] = example['true_answer'] == example['generated_answer']
    return example

def add_labels(example, true_labels, pred_labels, index):
    example['true_answer'] = true_labels[index]
    example['generated_answer'] = pred_labels[index]
    return example

true_labels = []
pred_labels = []

def evaluate_Idefics2(dataset, batch_size=16):
    keys = list(dataset.keys())

    for i in range(0, len(dataset['sample_index']), batch_size):
    # for i in range(0, 2, batch_size):
        batch = {key: dataset[key][i:i + batch_size] for key in keys}

        for j in range(len(batch['sample_index'])):
            data = {key: batch[key][j] for key in keys}
            if "answer" not in data:
                continue

            question = data["query_cot"]
            answer = str(data["answer"]).replace("The answer is: ", "")
            true_labels.append(answer)

            prompt_text = prompt + f"Q: {question}\nA:"
            prompt_text_with_image = prompt_text.replace("{question}", "<image> " + "{question}")
            inputs = processor(text=prompt_text_with_image, images=dataset['image'][i + j], return_tensors="pt")

            inputs = {k: v.to(device) for k, v in inputs.items()}

            with torch.no_grad():
                output_ids = model.generate(**inputs, max_new_tokens=500)
            output_text = processor.decode(output_ids[0], skip_special_tokens=True)
            generated_answer = extract_answer(output_text)
            pred_labels.append(generated_answer)

            print(f"Question: {question}")
            print(f"Output Text: {output_text}")
            print(f"Generated Answer: {generated_answer}")
            print(f"True Answer: {answer}")
            print("---")

            del inputs
            del output_ids
            torch.cuda.empty_cache()

    accuracy = accuracy_score(true_labels, pred_labels)
    f1 = f1_score(true_labels, pred_labels, average='weighted')
    precision = precision_score(true_labels, pred_labels, average='weighted')
    recall = recall_score(true_labels, pred_labels, average='weighted')

    # # 서브셋 및 라벨 추가
    # subset = dataset.select(range(0, len(true_labels)))  # 전체 true_labels 길이로 서브셋 선택
    # final_subset = subset.map(lambda x, idx: add_labels(x, true_labels, pred_labels, idx), with_indices=True)
    # final_subset = final_subset.map(compare_answers)
    print(f"Accuracy: {accuracy * 100:.2f}%")
    print(f"f1: {f1 * 100:.2f}%")
    print(f"precision: {precision * 100:.2f}%")
    print(f"recall: {recall * 100:.2f}%")

    return accuracy, f1, precision, recall


In [ ]:
print(true_labels)
print(pred_labels)

[]
[]


In [ ]:
evaluate_Idefics2(train_dataset)

스트리밍 출력 내용이 길어서 마지막 5000줄이 삭제되었습니다.
A:To solve this problem, we can use the Pythagorean theorem. Let's denote the distance from Phoenix to Atlanta as x. Then, the distance from Des Moines to Phoenix is 3482 - x, and the distance from Atlanta to Des Moines is 3482 - x. Using the Pythagorean theorem, we have:
(3482 - x)^2 + x^2 = (3482 - x) * (3482 - x)
3482^2 - 2 * 3482 * x + x^2 = 3482^2 - 2 * 3482 * x + x^2
2 * x^2 = 0
x^2 = 0
x = 0
The distance from Phoenix to Atlanta is 0 miles. The answer is: B.
Generated Answer: B
True Answer: D
---
Question: Please first conduct reasoning, and then answer the question and provide the final value, e.g., 1, 2.5, 300, at the end.
Question: Find the surface area of the following hemisphere.

Round your answer to two decimal places.
Output Text: 

Q: Please first conduct reasoning, and then answer the question and provide the final value, e.g., 1, 2.5, 300, at the end. Write the equation for the piecewise function symmetric to x=3, which goes through 

# inference & evaluation (w/key-value caching)

In [ ]:
def get_llama_response(message: str, history: list):

    if history is None:

        history = []

    print(history)

    query = format_message(message, history)  # tensor 형태로 나옴.


    output_ids = query

    past_key_values = None
    starting_position = output_ids.shape[1]

    partial_messages = ""

    with torch.no_grad():

        for _ in range(300):  # Increase the number of iterations

            if past_key_values is None:

                outputs = model(input_ids=output_ids, use_cache=True)

            else:

                outputs = model(input_ids=output_ids[:, -1:], past_key_values=past_key_values, use_cache=True)

​
            next_token_logits = outputs.logits[:, -1, :]

            next_token_id = torch.argmax(next_token_logits, dim=-1).unsqueeze(-1)

            output_ids = torch.cat([output_ids, next_token_id], dim=-1)

            partial_messages = tokenizer.decode(token_ids= output_ids[0][starting_position:], skip_special_tokens=True)

            past_key_values = outputs.past_key_values

​

            yield partial_messages